# mul 重写

In [1]:
import tvm
from tvm import relax
from tvm.relax.testing import nn
from tvm_book.nn import modules
from tvm.script import ir as I, relax as R, tir as T

测试当乘法算子的右操作数不是常量时的量化处理逻辑。

In [6]:
bb = relax.BlockBuilder()

with bb.function("main"):
    model = modules.Conv2D(16, 16, kernel_size=(3, 3), padding=(1, 1))
    x = nn.Placeholder((1, 16, 64, 64), dtype="float32", name="x")
    data = nn.Placeholder((1, 16, 1, 1), dtype="float32", name="const")
    multiplier = R.sigmoid(data)
    conv = model(x)
    act = R.nn.relu(data=conv)
    output = act * multiplier
    params = [x, data] + model.parameters()
    bb.emit_func_output(output, params)
mod = bb.get()

In [7]:
mod.show()